In [1]:
# import sys
# sys.path.append('/home/dp/Desktop/Bit/Bit_BP_new/')
# from Get_available_gpus import get_available_gpus
# print(get_available_gpus())

In [2]:
import os
os.environ['CUDA_VISIBLE_DEVICES']='0,1,2,3,5,7'
import numpy as np
import pandas as pd
import warnings
warnings.filterwarnings("ignore")
from keras.models import load_model
from keras.callbacks import ModelCheckpoint
from sklearn import preprocessing
from keras import backend as bek
from keras.optimizers import Adam
import gc
%matplotlib inline

Using TensorFlow backend.


#### Import hybriod induction learning model

In [3]:
import sys
sys.path.append('/home/dp/Desktop/Bit/Bit_BP_new/model_codes')
from IL import Induction_Learning as IL
from HIL_TL import HIL_TransferLearning as HIL_TL

In [4]:
# """
# data cell
# """
# #df1=pd.read_csv('/home/dp/Desktop/Bit/datapath/pair_end_merge_SYS_random_400_split_up.csv',index_col=0)## SYS
# df1=pd.read_csv('/home/dp/Desktop/Bit/datapath/pair_end_merge_DIA_random_400_split_down.csv',index_col=0)# DIA


In [5]:
# for i,item in enumerate(df1['DIA']):
#     '''
#     Repleace DIA by SYS when you run Systolic
#     '''
#     if(df1['time'].iloc[i]==2):
#         continue
#     elif(df1['time'].iloc[i]==1):
#         temp=df1[(df1['Person No']==df1['Person No'].iloc[i])&(df1['time']==2)]['DIA']
#         if(temp.empty):
#             continue
#         else:
#             print(df1['DIA'].iloc[i],temp.iloc[0])
#             df1['DIA'].iloc[i]=temp.iloc[0]
#     else:
#         continue

In [6]:
# cond2 = df1['count']!=0
# df1 = df1[cond2]

# #normalize
# target = 'DIA'# SYS

In [7]:
df1=pd.read_csv('/home/dp/Desktop/Bit/Bit_BP_new/datapath/pair_end_merge_DIA_random_400_split_down_hybrid_database.csv')

target = 'DIA'

print(df1.shape)

(84064, 831)


In [8]:
def test_step(train_temp,valid_temp, test_temp, testNo_temp, testtime_temp):
    X_train_s = train_temp.iloc[:,17:423]
    X_valid_s = valid_temp.iloc[:,17:423]
    X_test_s = test_temp.iloc[:,17:423]
    '''
    Training data
    '''
    f1=['DIA']
    Y_train = train_temp[f1]
    Y_train = scalert.transform(Y_train)
    
    # reshape train data
    X_train_r_s = np.zeros((len(X_train_s), 406, 1))
    X_train_r_s[:, :, 0] = X_train_s
    '''
    Validation data
    '''
    f2 = ['DIA']
    Y_valid = valid_temp[f2]
    Y_valid = scalert.transform(Y_valid)
    
    # reshape validation data
    X_valid_r_s = np.zeros((len(X_valid_s), 406, 1))
    X_valid_r_s[:,:,0] = X_valid_s
    ''' 
    testing data
    '''
    # reshape vali data
    X_test_r_s = np.zeros((len(X_test_s), 406, 1))
    X_test_r_s[:, :, 0] = X_test_s
    
    #fit
    '''
    - if directory for saving weight not exist, create a directory using testing subject number
    - each test subject best weight is saved with a file name with person number and round
    '''
    saveweight_path = os.makedirs('DIA/BestWeights/Person_' + str(testNo_temp),exist_ok=True)
    checkpoint_filepath='DIA/BestWeights/Person_' + str(testNo_temp) +'/'+ 'weights_best_Person_' + str(testNo_temp)+'_round_' + str(testtime_temp)+'.hdf5'
    checkpoint = ModelCheckpoint(checkpoint_filepath, monitor='loss', verbose=1, save_best_only=True,mode='min')
    callbacks_list = [checkpoint]
    
    model= IL(No_gpus=6)
    history = model.fit([X_train_r_s], Y_train, epochs=n_epochs, batch_size=batch_s,callbacks=callbacks_list,verbose=1)
    # save loss values
    df_loss = pd.DataFrame(history.history)
    ### loss path
    '''
    - if directory for saving train and validation loss not exist, create a directory using testing subject number
    - each training loss for each testing person and round is save with a file name indicating person number and rounds
    '''
    saveloss_path = os.makedirs('DIA/Loss_results/Person_' + str(testNo_temp),exist_ok=True)
    loss_filepath ='DIA/Loss_results/Person_' + str(testNo_temp) +'/'+ 'train_valid_loss_dia_Person_' + str(testNo_temp)+'_round_' + str(testtime_temp)+'.csv'
    df_loss.to_csv(loss_filepath, index = False)

    
    test_pred = model.predict([X_test_r_s])
    test_pred1 = scalert.inverse_transform(test_pred)
    test_temp['DIA_p']=test_pred1
    
    temp_a=0
    temp_b=0
    test_DIA_r=[]
    test_DIA_p=[]

    
    for i,item in enumerate(test_temp['Person No']):
        if((test_temp['Person No'].iloc[i]!=temp_a) | (test_temp['time'].iloc[i]!=temp_b)):
            
            #administrator mode
            test_DIA_r.append(test_temp['DIA'].iloc[i])
            temp = test_temp[(test_temp['Person No']==test_temp['Person No'].iloc[i])&(test_temp['time']==test_temp['time'].iloc[i])]
            t = np.median(temp['DIA_p'])
            test_DIA_p.append(t)
            temp_a = test_temp['Person No'].iloc[i]
            temp_b = test_temp['time'].iloc[i]

            
    print(test_DIA_p)
    print(test_DIA_r)
    del model
    bek.clear_session()
    gc.collect()
    return (test_DIA_p,test_DIA_r)

In [9]:
def test_step1(train_temp,valid_temp, test_temp, testNo_temp, testtime_temp):
    X_train_s = train_temp.iloc[:,17:423]
    X_valid_s = valid_temp.iloc[:,17:423]
    X_test_s = test_temp.iloc[:,17:423]
    '''
    Training data
    '''
    f1=['DIA']
    Y_train = train_temp[f1]
    Y_train = scalert.transform(Y_train)
    
    # reshape train data
    X_train_r_s = np.zeros((len(X_train_s), 406, 1))
    X_train_r_s[:, :, 0] = X_train_s
    '''
    Validation data
    '''
    f2 = ['DIA']
    Y_valid = valid_temp[f2]
    Y_valid = scalert.transform(Y_valid)
    
    # reshape validation data
    X_valid_r_s = np.zeros((len(X_valid_s), 406, 1))
    X_valid_r_s[:,:,0] = X_valid_s
    '''
    testing data
    '''
    # reshape vali data
    X_test_r_s = np.zeros((len(X_test_s), 406, 1))
    X_test_r_s[:, :, 0] = X_test_s
    
    #fit
    model1=IL(No_gpus=6)
    '''
    - call each test subject best weight in the saved directory with a file name as a person number and round
    '''
    checkpoint_filepath='DIA/BestWeights/Person_' + str(testNo_temp) +'/'+ 'weights_best_Person_' + str(testNo_temp)+'_round_' + str(testtime_temp)+'.hdf5'
    model1.load_weights(checkpoint_filepath, by_name = True)

    
    test_pred = model1.predict([X_test_r_s])
    test_pred1 = scalert.inverse_transform(test_pred)
    test_temp['DIA_p']=test_pred1
    
    temp_a=0
    temp_b=0
    test_DIA_r=[]
    test_DIA_p=[]

    
    for i,item in enumerate(test_temp['Person No']):
        if((test_temp['Person No'].iloc[i]!=temp_a) | (test_temp['time'].iloc[i]!=temp_b)):
            
            #administrator mode
            test_DIA_r.append(test_temp['DIA'].iloc[i])
            temp = test_temp[(test_temp['Person No']==test_temp['Person No'].iloc[i])&(test_temp['time']==test_temp['time'].iloc[i])]
            t = np.median(temp['DIA_p'])
            test_DIA_p.append(t)
            temp_a = test_temp['Person No'].iloc[i]
            temp_b = test_temp['time'].iloc[i]

            
    print(test_DIA_p)
    print(test_DIA_r)
    
    del model1
    bek.clear_session()
    gc.collect()
    
    return (test_DIA_p,test_DIA_r)

In [10]:
batch_s = 3000
n_epochs = 1000

In [11]:
################
testingNo_all = [1273,543,1002,342,245,149,1888,1373,1020,1775,1598, 1436, 1722, 2095, 2096]# 
################

for testingNo in testingNo_all:

    test_p=[]
    test_r=[]
    
    test_p_best=[]
    test_r_best=[]
    
    for test_time in range(10,16):
        test  = df1[(df1['count']==testingNo)&(df1['count_time']==test_time)]
        train = df1
        if(test.empty):
            continue
        else:
            test_data_future = df1[(df1['count']==testingNo)&(df1['count_time']>=test_time)]
            print(f'future data shape : {test_data_future.shape}')
            test_data_future_index = test_data_future.index
            train = train.drop(test_data_future_index)
            print(f'Train shape : {train.shape}')
            #print('Train shape : ', train.shape[0] + test.shape[0])
            '''
            - Choose a validation set
            - validation set is selected from subjects having rounds >=8
            - from subjects round 8 to 11, the last round is considered as a validation set
            - from subjects with rounds 12 and above, the last two successive rounds were considered as a validation set
            '''
            persons_last_round8 = set(train[train['count_time']>=8]['count'])-set(train[train['count_time']>=9]['count'])
            persons_last_round9 = set(train[train['count_time']>=9]['count'])-set(train[train['count_time']>=10]['count'])
            persons_last_round10 = set(train[train['count_time']>=10]['count'])-set(train[train['count_time']>=11]['count'])
            persons_last_round11 = set(train[train['count_time']>=11]['count'])-set(train[train['count_time']>=12]['count'])
            persons_last_round12 = set(train[train['count_time']>=12]['count'])-set(train[train['count_time']>=13]['count'])
            persons_last_round13 = set(train[train['count_time']>=13]['count'])-set(train[train['count_time']>=14]['count'])
            persons_last_round14 = set(train[train['count_time']>=14]['count'])-set(train[train['count_time']>=15]['count'])
            persons_last_round15 = set(train[train['count_time']>=15]['count'])
            validation = []
            for valid_person8 in persons_last_round8:
                valid8 = train[(train['count'] == valid_person8)&(train['count_time']==8)]
                validation.append(valid8)
            for valid_person9 in persons_last_round9:
                valid9 = train[(train['count'] == valid_person9)&(train['count_time']==9)]
                validation.append(valid9)
            for valid_person10 in persons_last_round10:
                valid10 = train[(train['count'] == valid_person10)&(train['count_time']==10)]
                validation.append(valid10)
            for valid_person11 in persons_last_round11:
                valid11 = train[(train['count'] == valid_person11)&(train['count_time']==11)]
                validation.append(valid11)
            for valid_person12 in persons_last_round12:
                valid12 = train[(train['count'] == valid_person12)&(train['count_time']>=11)]
                validation.append(valid12)
            for valid_person13 in persons_last_round13:
                valid13 = train[(train['count'] == valid_person13)&(train['count_time']>=12)]
                validation.append(valid13)
            for valid_person14 in persons_last_round14:
                valid14 = train[(train['count'] == valid_person14)&(train['count_time']>=13)]
                validation.append(valid14)
            for valid_person15 in persons_last_round15:
                valid15 = train[(train['count'] == valid_person15)&(train['count_time']>=14)]
                validation.append(valid15)
            validation_data = pd.concat(validation)
            validation_data_index = validation_data.index
            train = train.drop(validation_data_index)
            t = train[target]
            t = t.values.reshape(-1, 1)
            scalert = preprocessing.MinMaxScaler().fit(t)
            (temp_pred,temp_real) = test_step(train,validation_data, test,testingNo,test_time)
            (temp_pred_best,temp_real_best) = test_step1(train,validation_data,test,testingNo,test_time)
            
            test_p.append(temp_pred)
            test_r.append(temp_real)
            
            test_p_best.append(temp_pred_best)
            test_r_best.append(temp_real_best)
            
    d = {'DIA_real': test_r, 'DIA_pred': test_p}
    df_f = pd.DataFrame(data = d)
    
    ind =[]
    for j in range(2,len(df_f.index)+2):
        ind.append(j)
    
    df_f.index=ind
    
    name_temp =str(testingNo)+'-1000-256.csv'
    df_f.to_csv('DIA/' + name_temp)
    
    
    d_best = {'DIA_real': test_r_best, 'DIA_pred': test_p_best}
    df_f_best = pd.DataFrame(data = d_best)
    
    ind =[]
    for j in range(2,len(df_f_best.index)+2):
        ind.append(j)
    
    df_f_best.index=ind
    
    name_temp_best =str(testingNo)+'-1000-256-best.csv'
    df_f_best.to_csv('DIA/' + name_temp_best)

future data shape : (1091, 831)
Train shape : (82973, 831)
Epoch 1/1000
78871/78871 [==============================] - 51s 642us/step - loss: 1009.5656

Epoch 00001: loss improved from inf to 1009.56556, saving model to DIA/BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 2/1000
78871/78871 [==============================] - 28s 349us/step - loss: 0.1143

Epoch 00002: loss improved from 1009.56556 to 0.11427, saving model to DIA/BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 3/1000
78871/78871 [==============================] - 27s 348us/step - loss: 0.0364

Epoch 00003: loss improved from 0.11427 to 0.03645, saving model to DIA/BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 4/1000
78871/78871 [==============================] - 27s 349us/step - loss: 0.0302

Epoch 00004: loss improved from 0.03645 to 0.03018, saving model to DIA/BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 5/1000
78871/78871 [======